<div style="width: 100%; clear: both;">
    <div style="float: left; width: 50%;">
       <img src="https://raw.githubusercontent.com/JulioUQ/folium-gestion-pesquera/main/img/logo-datascience.png", align="left">
    </div>
</div>

<div style="float: right; width: 50%;">
    <p style="margin: 0; padding-top: 22px; text-align:right;">Julio Úbeda Quesada</p>
    <p style="margin: 0; text-align:right;">Científico de datos y especialista en machine learning</p>
    <p style="margin: 0; text-align:right; padding-button: 100px;">Manual de aprendizaje - Creación de mapas interactivos</p>
</div>

</div>
<div style="width: 100%; clear: both;">
<div style="width:100%;">&nbsp;</div>

# **Creación de Mapas Interactivos en Python**

En el notebook anterior aprendimos a crear mapas básicos con Folium, agregando marcadores simples, popups, tooltips e iconos personalizados.

En este cuaderno avanzaremos un paso más para trabajar con capas y controles, lo que nos permitirá:
- Organizar mejor la información en nuestros mapas.
- Activar o desactivar grupos de elementos de manera interactiva.
- Representar datos más complejos mediante polígonos y líneas.
- Añadir controles de visibilidad que faciliten la exploración de la información.
- Representar y explorar las trajectorias de manera dinámica y animada.

El objetivo de este notebook es que logres construir mapas dinámicos y más profesionales, capaces de integrar múltiples tipos de datos y personalizar la experiencia del usuario.

<ul style="list-style-type:none">

<li><a href="#1-capas-y-controles">1. Capas y Controles</a></li>
  <ul style="list-style-type:none">
    <li><a href="#1-1-capas-de-marcadores-folium-featuregroup">1.1. Capas de marcadores (<em>folium.FeatureGroup</em>)</a></li>
    <li><a href="#1-2-capas-de-poligonos-y-lineas-folium-polygon-y-folium-polyline">1.2. Capas de polígonos y líneas (<em>folium.Polygon</em>, <em>folium.PolyLine</em>)</a></li>
    <li><a href="#1-3-control-de-capas-y-visibilidad-folium-layercontrol">1.3. Control de capas y visibilidad (<em>folium.LayerControl</em>)</a></li>
  </ul>

<li><a href="#2-integracion-con-datos">2. Integración con Datos</a></li>
  <ul style="list-style-type:none">
    <li><a href="#2-1-importar-datos-desde-csv-con-pandas">2.1. Importar datos desde CSV con Pandas</a></li>
    <li><a href="#2-2-visualizacion-de-datos-con-geojson">2.2. Visualización de datos con GeoJSON</a></li>
    <li><a href="#2-3-mapas-coropleticos-folium-choropleth">2.3. Mapas coropléticos (<em>folium.Choropleth</em>)</a></li>
  </ul>

<li><a href="#3-personalizacion-avanzada">3. Personalización Avanzada</a></li>
  <ul style="list-style-type:none">
    <li><a href="#3-1-colores-y-estilos-dinamicos">3.1. Colores y estilos dinámicos</a></li>
    <li><a href="#3-2-rutas-y-puntos-destacados">3.2. Rutas y puntos destacados</a></li>
    <li><a href="#3-3-ruta-animada-en-el-tiempo-con-TimestampedGeoJson">3.3. Ruta animada en el tiempo con TimestampedGeoJson</a></li>
  </ul>

</ul>


<a id="1-capas-y-controles"></a>
# 1. Capas y Controles

En Folium, las capas son elementos que podemos superponer o alternar en un mapa. Esto incluye marcadores, líneas, polígonos, imágenes y datos geoespaciales.


<a id="1-1-capas-de-marcadores-folium-featuregroup"></a>
## 1.1. Capas de marcadores folium.FeatureGroup

Se crea un FeatureGroup, que actúa como una capa lógica para agrupar elementos (en este caso, marcadores de ciudades). 
- El argumento name define cómo aparecerá esta capa en el control de capas del mapa.

In [37]:
import folium

mapa = folium.Map(location=[40, -3], zoom_start=5)

capas_ciudades = folium.FeatureGroup(name="Ciudades")
folium.Marker([40.4168, -3.7038], popup="Madrid").add_to(capas_ciudades)
folium.Marker([41.3874, 2.1686], popup="Barcelona").add_to(capas_ciudades)

capas_ciudades.add_to(mapa)

mapa


<a id="1-2-capas-de-poligonos-y-lineas-folium-polygon-y-folium-polyline"></a>
## 1.2. Capas de polígonos y líneas folium.Polygon y folium.PolyLine

En Folium no solo podemos trabajar con marcadores puntuales, sino que también tenemos la posibilidad de representar rutas mediante líneas (`PolyLine`) y áreas mediante polígonos (`Polygon`). Estas funciones nos permiten añadir al mapa elementos más complejos que los simples puntos, enriqueciendo así la visualización.

En el siguiente ejemplo añadimos tres tipos de información:
- Un marcador en la Plaza Mayor de Madrid.
- Una ruta turística que conecta algunos puntos de interés (Puerta del Sol, Plaza Mayor y Retiro).
- Un polígono que delimita un área concreta dentro de la ciudad.

In [38]:
m = folium.Map(location=[40.4168, -3.7038], zoom_start=12, tiles="CartoDB positron")

# Grupo de marcadores
marker_layer = folium.FeatureGroup(name="Puntos de interés")

marker_layer.add_child(
    folium.Marker([40.4183, -3.7028], popup="Puerta del Sol", tooltip="Centro de Madrid")
)
marker_layer.add_child(
    folium.Marker([40.4138, -3.6922], popup="Parque del Retiro", tooltip="Área verde")
)

marker_layer.add_child(
    folium.Marker([40.4154, -3.7074], popup="Plaza Mayor", tooltip="Plaza")
)

m.add_child(marker_layer)

ruta = folium.FeatureGroup(name="Ruta turística")

ruta.add_child(
    folium.PolyLine(
        locations=[
            [40.4183, -3.7028],  # Puerta del Sol
            [40.4154, -3.7074],  # Plaza Mayor
            [40.4138, -3.6922]   # Retiro
        ],
        color="blue",
        weight=4,
        opacity=0.7
    )
)

m.add_child(ruta)

poligono = folium.FeatureGroup(name="Área destacada")

poligono.add_child(
    folium.Polygon(
        locations=[
            [40.42, -3.71],
            [40.42, -3.69],
            [40.40, -3.69],
            [40.40, -3.71]
        ],
        color="green",
        fill=True,
        fill_opacity=0.4,
        tooltip="Zona delimitada"
    )
)

m.add_child(poligono)



Con este tipo de capas podemos ir más allá de la representación básica de puntos. Las líneas nos sirven, por ejemplo, para mostrar recorridos o trayectorias, mientras que los polígonos son útiles para delimitar áreas de interés como barrios, zonas protegidas o superficies de estudio.

<a id="1-3-control-de-capas-y-visibilidad-folium-layercontrol"></a>
## 1.3. Control de capas y visibilidad folium.LayerControl

Cuando trabajamos con varias capas en un mismo mapa, es importante ofrecer al usuario la posibilidad de activar o desactivar cada una de ellas según le interese. Para ello Folium nos proporciona la función `LayerControl`, que añade un panel de control en el mapa desde el que podemos gestionar la visibilidad de todas las capas que hayamos definido previamente.

En este ejemplo lo añadimos de forma muy sencilla:

In [39]:
folium.LayerControl().add_to(m)

m.save("../img/elementos_folium.html")

m


Con esta instrucción se habilita un cuadro de control en la esquina superior derecha del mapa. A partir de ahí, podemos mostrar u ocultar los distintos grupos de elementos (marcadores, rutas, polígonos, etc.) con un simple clic. Esto resulta especialmente útil cuando el mapa contiene mucha información y queremos que la visualización sea lo más clara y flexible posible.

<a id="2-integracion-con-datos"></a>
# 2. Integración con Datos

<a id="2-1-importar-datos-desde-csv-con-pandas"></a>
## 2.1. Importar datos desde CSV con Pandas

En muchas ocasiones los datos que vamos a representar en el mapa no los introducimos manualmente, sino que proceden de ficheros externos. Una de las formas más habituales de almacenar y compartir información tabular es el formato CSV (valores separados por comas o punto y coma).

Con la librería Pandas podemos importar fácilmente este tipo de archivos y trabajar con ellos como tablas en memoria. En el siguiente ejemplo leemos un conjunto de posiciones de barcos pesqueros a partir de un fichero CSV:

In [40]:
import pandas as pd

# Leer datos
df = pd.read_csv("../data/Puntos VMS/Posiciones_Atuneros-Cañeros-Canarias.csv", sep=";", decimal=",")  
df

IDBUQUE  IDLOCALIZADOR  IdPosicion                       FcIval  \
0     43613           4789   237098219  2022-09-13 07:01:00.0010000   
1     43613           4789   237103572  2022-09-13 11:01:00.0010000   
2     43613           4789   237106257  2022-09-13 13:01:00.0010000   
3     43613           4789   237109231  2022-09-13 15:02:00.0010000   
4     43613           4789   237111763  2022-09-13 17:01:00.0010000   
..      ...            ...         ...                          ...   
69    43613           4789   237261210  2022-09-18 23:01:00.0010000   
70    43613           4789   237263439  2022-09-19 01:01:00.0010000   
71    43613           4789   237287810  2022-09-19 19:01:00.0010000   
72    43613           4789   237290102  2022-09-19 21:01:00.0010000   
73    43613           4789   237292306  2022-09-19 23:01:00.0010000   

                         FcFval  \
0   2022-09-13 09:01:00.0000000   
1   2022-09-13 13:01:00.0000000   
2   2022-09-13 15:02:00.0000000   
3   2022-09-13 17:01:00.0000000   
4   2022-09-13 19:01:00.0000000   
..                          ...   
69  2022-09-19 01:01:00.0000000   
70  2022-09-19 03:01:00.0000000   
71  2022-09-19 21:01:00.0000000   
72  2022-09-19 23:01:00.0000000   
73  2022-09-20 01:01:00.0000000   

                                              Geom  Rumbo  Velocidad  Suceso  \
0   0xE6100000010CF9FFFF5FF2CB30C0000000A07F233C40    334        9.6       0   
1   0xE6100000010C09000080AFF930C0020000E051383C40    328        5.2       0   
2   0xE6100000010C070000A0D53131C0FEFFFF7F4E5B3C40    257        6.8       0   
3   0xE6100000010C0D000040536A31C007000000564E3C40    243        7.4       0   
4   0xE6100000010CFBFFFF7F939831C0010000C0C8363C40    182        2.2       0   
..                                             ...    ...        ...     ...   
69  0xE6100000010CF5FFFF3F26B830C00100002031083C40    279        0.4       0   
70  0xE6100000010CF8FFFF3FA9B830C001000020F9053C40      0        0.0       0   
71  0xE6100000010CF6FFFFBF679830C0F8FFFF3FA9F83B40    106        8.8       0   
72  0xE6100000010C040000002B4730C0F8FFFFDFD0E23B40    112        8.6       0   
73  0xE6100000010CEBFFFF5F66E62FC0F5FFFF9F6ED23B40    111        8.4       0   

    IdZonaPortuaria    Latitud   Longitud   Año  Mes  
0               NaN  28.138666 -16.796667  2022    9  
1               NaN  28.219999 -16.975334  2022    9  
2               NaN  28.356667 -17.194666  2022    9  
3               NaN  28.306000 -17.415333  2022    9  
4               NaN  28.214001 -17.596001  2022    9  
..              ...        ...        ...   ...  ...  
69              NaN  28.032000 -16.719334  2022    9  
70              NaN  28.023333 -16.721333  2022    9  
71              NaN  27.971333 -16.595333  2022    9  
72              NaN  27.886000 -16.278000  2022    9  
73              NaN  27.822001 -15.950000  2022    9  

[74 rows x 14 columns]

Una vez que hemos importado nuestro fichero CSV a un DataFrame, podemos representar cada fila como un punto en el mapa. Hasta ahora hemos usado `folium.Marker`, que muestra el típico marcador con forma de “pin”. Sin embargo, si tenemos muchos registros este icono puede saturar el mapa.

En estos casos resulta más conveniente usar `folium.CircleMarker`, que nos permite representar cada posición con un círculo sencillo y configurable (color, tamaño, opacidad, etc.). A continuación lo aplicamos a nuestro conjunto de datos, dibujando cada posición de barco como un círculo azul:

In [41]:
m = folium.Map(location=[df.Latitud.mean(), df.Longitud.mean()], 
               zoom_start=6, 
               tiles="CartoDB positron"
               )

# Añadir marcadores 
for _, row in df.iterrows():
    folium.CircleMarker(
        location=[row.Latitud, row.Longitud],
        radius=4,                # tamaño del círculo
        color="blue",            # color del borde
        fill=True,
        fill_color="blue",       # color de relleno
        fill_opacity=0.6,        # transparencia
        popup=f"<b>{row.Rumbo}</b><br>{row.Velocidad}",
        tooltip=row.FcIval
    ).add_to(m)

m.save("../img/posiciones_vms.html")

m

De esta forma conseguimos una visualización más limpia y homogénea:
- Cada punto se muestra como un círculo azul, pequeño pero bien visible.
- Seguimos conservando la información extra en los popups y tooltips, de manera que podemos explorar los datos interactuando con el mapa.

<a id="2-2-visualizacion-de-datos-con-geojson"></a>
## 2.2. Visualización de datos con GeoJSON

Además de trabajar con puntos procedentes de tablas, también podemos representar en el mapa capas espaciales completas a partir de ficheros vectoriales como `shapefiles` o `GeoJSON`. Para ello resulta muy útil la librería GeoPandas, que nos permite leer estos formatos y convertirlos en GeoDataFrame, es decir, tablas que incluyen geometrías (puntos, líneas o polígonos).

En el siguiente ejemplo cargamos un `shapefile` con los Rectángulos Estadísticos ICES y lo representamos directamente en un mapa de Folium:

In [ ]:
import geopandas as gpd

# Leer shapefile con GeoPandas
gdf = gpd.read_file("../data/Rectangulos Estadisticos ICES/RectangulosEstadisticosICES.shp")

# Crear mapa base
m = folium.Map(location=[40.4168, -3.7038], 
               zoom_start=5, 
               tiles="CartoDB positron")

# Añadir geometrías con tooltip y popup
folium.GeoJson(
    gdf,
    name="Rectángulos ICES",
    tooltip=folium.GeoJsonTooltip(
        fields=["IdRectangu", "Descripcio"], 
        aliases=["ID:", "Descripción:"]
    ),
    popup=folium.GeoJsonPopup(
        fields=["IdRectangu", "Descripcio", "Sur", "Oeste", "Norte", "Este"],
        aliases=["ID:", "Descripción:", "Sur:", "Oeste:", "Norte:", "Este:"]
    )
).add_to(m)

m.save("../img/mapa_geopandas.html")
m

Con esta configuración:
- El tooltip muestra de forma rápida el ID y la descripción al pasar el ratón sobre el rectángulo.
- El popup despliega todos los detalles (incluyendo límites geográficos) cuando hacemos clic.

<a id="2-3-mapas-coropleticos-folium-choropleth"></a>
## 2.3. Mapas coropléticos folium.Choropleth

Los mapas coropléticos son una forma muy útil de representar información espacial cuando queremos visualizar cómo se distribuye un valor numérico a lo largo de diferentes áreas. En lugar de usar puntos o marcadores, coloreamos polígonos según el valor de una variable: por ejemplo, densidad de población, número de capturas, intensidad de esfuerzo pesquero, etc.

En Folium podemos crear este tipo de mapas con la función `folium.Choropleth`, que recibe tanto las geometrías (GeoJSON) como los valores que queremos representar.

En el siguiente ejemplo coloreamos los rectángulos estadísticos ICES en función de su coordenada Sur, de manera que observamos un gradiente de color según la posición latitudinal:

In [43]:
# Crear mapa base
m = folium.Map(location=[40.4168, -3.7038], 
               zoom_start=5, 
               tiles="CartoDB positron")

# Crear mapa coroplético
folium.Choropleth(
    geo_data=gdf,                # geometrías
    data=gdf,                    # datos asociados
    columns=["IdRectangu", "Sur"],  # campo clave y variable a representar
    key_on="feature.properties.IdRectangu",
    fill_color="YlGnBu",         # paleta de colores
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Coordenada Sur"
).add_to(m)

m.save("../img/rect_ices_coropletico.html")
m


**Explicación**

- `geo_data y data`: usamos el mismo GeoDataFrame, que contiene tanto las geometrías como los atributos.
- `columns`: especificamos el identificador único (IdRectangu) y el campo que queremos visualizar (Sur).
- `key_on`: conecta la geometría con el atributo usando el campo IdRectangu.
- `fill_color`: define la paleta de colores; en este caso YlGnBu (amarillo-verde-azul).
- `legend_name`: añade una leyenda para interpretar el gradiente de color.
  
De este modo cada rectángulo se colorea automáticamente según su valor en la columna Sur, facilitando la comparación visual en todo el mapa.

<a id="3-personalizacion-avanzada"></a>
# 3. Personalización Avanzada

<a id="3-1-colores-y-estilos-dinamicos"></a>
## 3.1. Colores y estilos dinámicos

Hasta ahora hemos representado los puntos con símbolos idénticos (círculos azules, por ejemplo). Sin embargo, a menudo nos interesa que el estilo de cada punto (color, tamaño u opacidad) dependa de alguna variable del dataset. Esto nos permite añadir una dimensión extra de información a la visualización.

Un caso típico es el de las trayectorias de barcos, donde podemos colorear los puntos en función de la velocidad: azul para velocidades bajas, amarillo para medias y rojo para altas. Así, además de ver la ruta del buque, podemos identificar rápidamente en qué zonas navega más rápido o más despacio.

En el siguiente ejemplo asignamos colores dinámicamente en función de la columna Velocidad:

In [ ]:
# Función para asignar color según velocidad
def color_por_velocidad(vel):
    if vel < 2:
        return "blue"     # baja velocidad
    elif vel < 5:
        return "orange"   # velocidad media
    else:
        return "red"      # alta velocidad

# Crear mapa base
m = folium.Map(
    location=[df.Latitud.mean(), df.Longitud.mean()],
    zoom_start=7,
    tiles="CartoDB positron"
)

# Crear capas por rango de velocidad
capa_baja = folium.FeatureGroup(name="Velocidad baja (<2 nudos)")
capa_media = folium.FeatureGroup(name="Velocidad media (2-5 nudos)")
capa_alta = folium.FeatureGroup(name="Velocidad alta (>5 nudos)")

# Añadir puntos a la capa correspondiente
for _, row in df.iterrows():
    marcador = folium.CircleMarker(
        location=[row.Latitud, row.Longitud],
        radius=5,
        color=color_por_velocidad(row.Velocidad),
        fill=True,
        fill_color=color_por_velocidad(row.Velocidad),
        fill_opacity=0.7,
        popup=f"<b>Velocidad:</b> {row.Velocidad} nudos<br>"
              f"<b>Rumbo:</b> {row.Rumbo}<br>"
              f"<b>Fecha:</b> {row.FcIval}",
        tooltip=f"Vel: {row.Velocidad} nudos"
    )
    
    if row.Velocidad < 2:
        marcador.add_to(capa_baja)
    elif row.Velocidad < 5:
        marcador.add_to(capa_media)
    else:
        marcador.add_to(capa_alta)

# Añadir capas al mapa
capa_baja.add_to(m)
capa_media.add_to(m)
capa_alta.add_to(m)

# Añadir control de capas
folium.LayerControl().add_to(m)

m.save("../img/mapa_colores_dinamicos_layers.html")
m


**Explicación**
- Creamos una función de estilo (color_por_velocidad) que devuelve un color según el valor de Velocidad.
- Cada punto se representa como un círculo con ese color.
- Los popups muestran información detallada (velocidad, rumbo y fecha).
- Los tooltips nos permiten ver rápidamente la velocidad al pasar el ratón.

De esta forma convertimos un simple conjunto de posiciones en una representación interactiva que refleja directamente el comportamiento del barco en el mar.

<a id="3-2-rutas-y-puntos-destacados"></a>
## 3.2. Rutas y puntos destacados

Para visualizar cómo se desplaza un buque a lo largo del tiempo, podemos dibujar una línea que conecte todas sus posiciones ordenadas cronológicamente y marcar el punto inicial y el punto final con iconos distintos. Esto nos permite ver claramente el recorrido completo y dónde empezó y terminó.

En este ejemplo representamos la trayectoria completa del buque conectando sus posiciones en orden temporal y, al mismo tiempo, coloreamos cada punto según su velocidad. Además, destacamos el primer punto y el último punto con iconos específicos para identificar inicio y fin de la ruta.

In [45]:
# Ordenar el DataFrame por fecha/hora
df_sorted = df.sort_values("FcIval")

# Función para asignar color según velocidad
def color_por_velocidad(vel):
    if vel < 2:
        return "blue"
    elif vel < 5:
        return "orange"
    else:
        return "red"

# Crear mapa base
m = folium.Map(
    location=[df_sorted.Latitud.mean(), df_sorted.Longitud.mean()],
    zoom_start=7,
    tiles="CartoDB positron"
)

# Crear capas por rango de velocidad para layer control
capa_baja = folium.FeatureGroup(name="Velocidad baja (<2 nudos)")
capa_media = folium.FeatureGroup(name="Velocidad media (2-5 nudos)")
capa_alta = folium.FeatureGroup(name="Velocidad alta (>5 nudos)")

# Lista de coordenadas para la línea de la ruta
ruta_coords = []

# Añadir puntos con colores dinámicos y asignarlos a la capa correspondiente
for _, row in df_sorted.iterrows():
    coord = [row.Latitud, row.Longitud]
    ruta_coords.append(coord)
    
    marcador = folium.CircleMarker(
        location=coord,
        radius=5,
        color=color_por_velocidad(row.Velocidad),
        fill=True,
        fill_color=color_por_velocidad(row.Velocidad),
        fill_opacity=0.7,
        popup=f"<b>Velocidad:</b> {row.Velocidad} nudos<br>"
              f"<b>Rumbo:</b> {row.Rumbo}<br>"
              f"<b>Fecha:</b> {row.FcIval}",
        tooltip=f"Vel: {row.Velocidad} nudos"
    )
    
    if row.Velocidad < 2:
        marcador.add_to(capa_baja)
    elif row.Velocidad < 5:
        marcador.add_to(capa_media)
    else:
        marcador.add_to(capa_alta)

# Añadir la línea de la ruta
folium.PolyLine(
    locations=ruta_coords,
    color="blue",
    weight=3,
    opacity=0.6,
    tooltip="Ruta del buque"
).add_to(m)

# Destacar primer y último punto con iconos especiales
primer_punto = df_sorted.iloc[0]
ultimo_punto = df_sorted.iloc[-1]

folium.Marker(
    location=[primer_punto.Latitud, primer_punto.Longitud],
    popup=f"<b>Primer punto</b><br>Vel: {primer_punto.Velocidad} nudos<br>Rumbo: {primer_punto.Rumbo}",
    icon=folium.Icon(color="green", icon="play"),
    tooltip="Inicio"
).add_to(m)

folium.Marker(
    location=[ultimo_punto.Latitud, ultimo_punto.Longitud],
    popup=f"<b>Último punto</b><br>Vel: {ultimo_punto.Velocidad} nudos<br>Rumbo: {ultimo_punto.Rumbo}",
    icon=folium.Icon(color="red", icon="flag"),
    tooltip="Fin"
).add_to(m)

# Añadir capas al mapa
capa_baja.add_to(m)
capa_media.add_to(m)
capa_alta.add_to(m)

# Añadir control de capas
folium.LayerControl().add_to(m)

m.save("../img/mapa_ruta_buque.html")
m


**Explicación**
- Cada punto de la ruta se colorea según su velocidad usando CircleMarker.
- Creamos FeatureGroups para cada rango de velocidad y los añadimos al LayerControl, de forma que podemos mostrar u ocultar cada grupo.
- La línea de la ruta conecta todas las posiciones para visualizar el recorrido completo.
- Se destacan el primer y último punto con iconos distintos para identificar inicio y fin.
- Los popups y tooltips permiten consultar la velocidad, rumbo y fecha de cada posición.

De esta manera, el mapa combina información temporal, trayectoria y datos dinámicos de velocidad, ofreciendo una visualización completa y clara del comportamiento del buque.

<a id="3-3-ruta-animada-en-el-tiempo-con-TimestampedGeoJson"></a>
## 3.3. Ruta animada en el tiempo con TimestampedGeoJson

In [46]:
from folium.plugins import TimestampedGeoJson

# Ordenar DataFrame por fecha/hora
df_sorted = df.sort_values("FcIval")

# Función para asignar color según velocidad
def color_por_velocidad(vel):
    if vel < 2:
        return "blue"
    elif vel < 5:
        return "orange"
    else:
        return "red"

# Crear mapa base
m = folium.Map(
    location=[df_sorted.Latitud.mean(), df_sorted.Longitud.mean()],
    zoom_start=7,
    tiles="CartoDB positron"
)

# Lista de coordenadas para la línea de ruta
ruta_coords = df_sorted[["Latitud", "Longitud"]].values.tolist()

# Dibujar línea de la ruta
folium.PolyLine(
    locations=ruta_coords,
    color="blue",
    weight=3,
    opacity=0.5,
    tooltip="Ruta del buque"
).add_to(m)

# Destacar primer y último punto con iconos especiales
primer_punto = df_sorted.iloc[0]
ultimo_punto = df_sorted.iloc[-1]

folium.Marker(
    location=[primer_punto.Latitud, primer_punto.Longitud],
    popup=f"<b>Primer punto</b><br>Vel: {primer_punto.Velocidad} nudos<br>Rumbo: {primer_punto.Rumbo}",
    icon=folium.Icon(color="green", icon="play"),
    tooltip="Inicio"
).add_to(m)

folium.Marker(
    location=[ultimo_punto.Latitud, ultimo_punto.Longitud],
    popup=f"<b>Último punto</b><br>Vel: {ultimo_punto.Velocidad} nudos<br>Rumbo: {ultimo_punto.Rumbo}",
    icon=folium.Icon(color="red", icon="flag"),
    tooltip="Fin"
).add_to(m)

# Crear GeoJSON temporal para animación de puntos por velocidad
features = []
for _, row in df_sorted.iterrows():
    features.append({
        "type": "Feature",
        "geometry": {
            "type": "Point",
            "coordinates": [row.Longitud, row.Latitud]
        },
        "properties": {
            "time": row.FcIval,
            "style": {"color": color_por_velocidad(row.Velocidad)},
            "icon": "circle",
            "popup": f"Vel: {row.Velocidad} nudos<br>Rumbo: {row.Rumbo}<br>Fecha: {row.FcIval}"
        }
    })

geojson = {
    "type": "FeatureCollection",
    "features": features
}

# Añadir animación temporal
TimestampedGeoJson(
    geojson,
    period="PT1H",
    add_last_point=True,
    auto_play=True,
    loop=False,
    max_speed=1,
    loop_button=True,
    date_options="YYYY-MM-DD HH:mm:ss",
    time_slider_drag_update=True
).add_to(m)

m.save("../img/mapa_ruta_animada.html")
m


**Explicación**
1. Línea de ruta: Conecta todas las posiciones para mostrar el recorrido completo.
2. Puntos destacados:
   - Primer punto → verde con icono “play” (inicio)
   - Último punto → rojo con icono “flag” (fin)
3. Puntos animados: Cada posición del buque se representa con TimestampedGeoJson, mostrando el color según la velocidad y los popups correspondientes.
4. Control temporal: La animación avanza siguiendo FcIval, permitiendo ver cómo evoluciona la ruta y las velocidades a lo largo del tiempo.
5. Interactividad: Popups y tooltips permiten consultar información de cada punto mientras se anima la ruta.